In [1]:
import timeit

In [2]:
from bs4 import BeautifulSoup as bs
import requests
import re
import numpy as np
import os
import pandas as pd
import selenium
import warnings
import time
from pathlib import Path
import sys
import datetime as datetime
#---------------------------------------------------------------
from selenium import webdriver
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains

In [3]:
url='https://www.themoviedb.org/movie/top-rated' #https://www.themoviedb.org/movie?language=en

In [4]:
driver=webdriver.Chrome('C:/Users/Luis/Documents/GitHub/chromedriver.exe') 
driver.get(url)
#---------------------------------------------------------------
ActionChains(driver).send_keys(Keys.END).perform()
time.sleep(2)
#---------------------------------------------------------------
WebDriverWait(driver, 10).until(EC.element_to_be_clickable(
    (By.XPATH, "//*[@id='pagination_page_1']/p/a"))).click()
time.sleep(2)
#---------------------------------------------------------------
for i in range(0,150): #CHANGE FOR NUMBER OF FILMS***************** anter era 20
    ActionChains(driver).send_keys(Keys.END).perform()
    time.sleep(0.5)
#---------------------------------------------------------------
pagweb=driver.page_source
driver.quit()

<ipython-input-4-bd11beecc5f7>:1: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver=webdriver.Chrome('C:/Users/Luis/Documents/GitHub/chromedriver.exe')


In [5]:
soup=bs(pagweb,'html') #GENERAL SOUP TOP MOVIES
soup

<html class="no-js k-webkit k-webkit107 nprogress-busy" lang="en"><head>
<title>Top Rated Movies — The Movie Database (TMDB)</title>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="on" http-equiv="cleartype"/>
<meta charset="utf-8"/>
<meta content="Movies, TV Shows, Streaming, Reviews, API, Actors, Actresses, Photos, User Ratings, Synopsis, Trailers, Teasers, Credits, Cast" name="keywords"/>
<meta content="yes" name="mobile-web-app-capable"/>
<meta content="yes" name="apple-mobile-web-app-capable"/>
<meta content="width=device-width,initial-scale=1" name="viewport"/>
<meta content="The Movie Database (TMDB) is a popular, user editable database for movies and TV shows." name="description"/>
<meta content="/assets/2/v4/icons/mstile-144x144-30e7905a8315a080978ad6aeb71c69222b72c2f75d26dab1224173a96fecc962.png" name="msapplication-TileImage"/>
<meta content="#032541" name="msapplication-TileColor"/>
<meta content="#032541" name="theme-color"/>
<link href="/assets/2/app

In [6]:
title_id=[]
for link in soup.find_all('a',class_="image",href=True):
    if link['href'].startswith('/movie/'):
        title_id.append(link['href'])
title_id

['/movie/238',
 '/movie/278',
 '/movie/240',
 '/movie/424',
 '/movie/19404',
 '/movie/129',
 '/movie/389',
 '/movie/372058',
 '/movie/496243',
 '/movie/497',
 '/movie/155',
 '/movie/724089',
 '/movie/696374',
 '/movie/553512',
 '/movie/680',
 '/movie/429',
 '/movie/611291',
 '/movie/13',
 '/movie/122',
 '/movie/769',
 '/movie/761053',
 '/movie/11216',
 '/movie/637',
 '/movie/346',
 '/movie/14537',
 '/movie/539',
 '/movie/311',
 '/movie/12477',
 '/movie/510',
 '/movie/550',
 '/movie/40096',
 '/movie/255709',
 '/movie/164558',
 '/movie/598',
 '/movie/324857',
 '/movie/92321',
 '/movie/378064',
 '/movie/4935',
 '/movie/1891',
 '/movie/568300',
 '/movie/120',
 '/movie/18491',
 '/movie/157336',
 '/movie/423',
 '/movie/599',
 '/movie/283566',
 '/movie/244786',
 '/movie/121',
 '/movie/73',
 '/movie/567',
 '/movie/20334',
 '/movie/3782',
 '/movie/27205',
 '/movie/807',
 '/movie/914',
 '/movie/644479',
 '/movie/774372',
 '/movie/128',
 '/movie/632632',
 '/movie/901',
 '/movie/361743',
 '/movie/

In [7]:
List_titles_url=['https://www.themoviedb.org' + title for title in title_id]
List_titles_url

['https://www.themoviedb.org/movie/238',
 'https://www.themoviedb.org/movie/278',
 'https://www.themoviedb.org/movie/240',
 'https://www.themoviedb.org/movie/424',
 'https://www.themoviedb.org/movie/19404',
 'https://www.themoviedb.org/movie/129',
 'https://www.themoviedb.org/movie/389',
 'https://www.themoviedb.org/movie/372058',
 'https://www.themoviedb.org/movie/496243',
 'https://www.themoviedb.org/movie/497',
 'https://www.themoviedb.org/movie/155',
 'https://www.themoviedb.org/movie/724089',
 'https://www.themoviedb.org/movie/696374',
 'https://www.themoviedb.org/movie/553512',
 'https://www.themoviedb.org/movie/680',
 'https://www.themoviedb.org/movie/429',
 'https://www.themoviedb.org/movie/611291',
 'https://www.themoviedb.org/movie/13',
 'https://www.themoviedb.org/movie/122',
 'https://www.themoviedb.org/movie/769',
 'https://www.themoviedb.org/movie/761053',
 'https://www.themoviedb.org/movie/11216',
 'https://www.themoviedb.org/movie/637',
 'https://www.themoviedb.org/movi

In [8]:
len(List_titles_url)

3040

In [9]:
start = timeit.default_timer()
def title_clean(raw_html):
    cleantitle = re.sub('\W?<.*?>| —.*','', raw_html)
    return cleantitle
#---------------------------------------------------------------
def top_movies_scrapper(x):
    response=requests.get(List_titles_url[x]).content
    source=bs(response,'html')
    Titles=source.find_all('title')
    return Titles
#---------------------------------------------------------------
def genres_function(x):
    response=requests.get(List_titles_url[x]).content
    source=bs(response,'html')
    genre=source.find_all('span',class_='genres')
    return genre    
#---------------------------------------------------------------
def duration_function(x):
    response=requests.get(List_titles_url[x]).content
    source=bs(response,'html')
    duration=source.find_all('span',class_='runtime')
    return duration
#---------------------------------------------------------------
def director_function(x):
    response=requests.get(List_titles_url[x]).content
    source=bs(response,'html')
    director=source.find_all('li',class_="profile")
    return director
#---------------------------------------------------------------
def cast_function(x):
    try:
         response=requests.get(List_titles_url[x]).content
         source=bs(response,'html')
         cast=source.find_all('li',class_="card")
         return cast
    except:
        return 'None'
#---------------------------------------------------------------
def budget_function(x):
    response=requests.get(List_titles_url[x]).content
    salsa=bs(response,'html').text
    salsa=salsa.split('\n')
    salsa=[element for element in salsa if element != '']
    
    index = [i for i, elem in enumerate(salsa) if 'Budget' in elem]
    budget=salsa[index[0]][len('Budget '):]
    return budget
#---------------------------------------------------------------
def revenues_function(x):
    response=requests.get(List_titles_url[x]).content
    salsa=bs(response,'html').text
    salsa=salsa.split('\n')
    salsa=[element for element in salsa if element != '']
    
    index = [i for i, elem in enumerate(salsa) if 'Revenue' in elem]
    revenue=salsa[index[0]][len('Revenue '):]
    return revenue
#---------------------------------------------------------------
def languages_function(x):
     response=requests.get(List_titles_url[x]).content
     salsa=bs(response,'html').text
     salsa=salsa.split('\n')
     salsa=[element for element in salsa if element != '']
    
     index = [i for i, elem in enumerate(salsa) if 'Original Language' in elem]
     language=salsa[index[0]][len('Original Language '):]
     return language
#---------------------------------------------------------------    
Title_list=[]
Genres=[]
Durations=[]
Directors=[]
Casts=[]
Budgets=[]
Revenues=[]
Languages=[]
#******************************************************************
#Returns the appended lists from above
for num_title in range(len(List_titles_url)):
#---------------------------------------------------------------    
    Title_list.append(title_clean(str(top_movies_scrapper(num_title))))
#---------------------------------------------------------------    
    Genre_clean=genres_function(num_title)
    Genres.append(Genre_clean)
    Genres[num_title]=re.findall(r'>(.+?)<', re.sub('>\W*?<','',str(Genres[num_title])))
#---------------------------------------------------------------    
    Durations.append(duration_function(num_title))
    Durations[num_title]=re.sub(r'<(.+?)>|\s*|\W*?','',str(Durations[num_title]))
#---------------------------------------------------------------    
    Directors.append(director_function(num_title))
    Directors[num_title]=re.findall(r'>(.+?)<', re.sub('>\W*?<','',str(Directors[num_title])))
    Directors[num_title]=Directors[num_title][0]
#---------------------------------------------------------------    
    Casts.append(cast_function(num_title))
    if Casts[num_title]!='None': #Casts[num_title][0]!='None':
        Casts[num_title]=re.findall(r'>(.+?)<', re.sub('>\W*?<','',str(Casts[num_title])))
        Casts[num_title]=Casts[num_title][0:4]
    else:
        Casts[num_title]=['None','None','None','None']
#---------------------------------------------------------------
    Budgets.append(budget_function(num_title))
    Revenues.append(revenues_function(num_title))
    Languages.append(languages_function(num_title))
#---------------------------------------------------------------
stop = timeit.default_timer()

print('Time: ', stop - start) 

Time:  7899.2744942


In [10]:
len(Casts)

3040

In [11]:
Lead_Actor_1=[]
Lead_Actor_2=[]
for element in range(len(Casts)):
    if Casts[element]:
        Lead_Actor_1.append(Casts[element][0])
        if len(Casts[element])==2:
            Lead_Actor_2.append('None')
        else:
            Lead_Actor_2.append(Casts[element][2])
    else:
        Lead_Actor_1.append('None')
        Lead_Actor_2.append('None')

In [12]:
Lead_Actor_1

['Marlon Brando',
 'Tim Robbins',
 'Al Pacino',
 'Liam Neeson',
 'Shah Rukh Khan',
 'Rumi Hiiragi',
 'Martin Balsam',
 'Ryunosuke Kamiki',
 'Song Kang-ho',
 'Tom Hanks',
 'Christian Bale',
 'Melanie Zanetti',
 'Melanie Zanetti',
 'Kim Nam-joon',
 'John Travolta',
 'Clint Eastwood',
 'Kim Nam-joon',
 'Tom Hanks',
 'Elijah Wood',
 'Ray Liotta',
 'Melanie Zanetti',
 'Philippe Noiret',
 'Roberto Benigni',
 'Toshirō Mifune',
 'Tatsuya Nakadai',
 'Anthony Perkins',
 'Robert De Niro',
 'Tsutomu Tatsumi',
 'Jack Nicholson',
 'Edward Norton',
 'Matheus Nachtergaele',
 'Sol Kyung-gu',
 'Harry Styles',
 'Alexandre Rodrigues',
 'Shameik Moore',
 'Izumi Sawada',
 'Miyu Irino',
 'Chieko Baisho',
 'Mark Hamill',
 'Kim Nam-joon',
 'Elijah Wood',
 'Megumi Ogata',
 'Matthew McConaughey',
 'Adrien Brody',
 'William Holden',
 'Megumi Ogata',
 'Miles Teller',
 'Elijah Wood',
 'Edward Norton',
 'James Stewart',
 'Margaret Sullavan',
 'Takashi Shimura',
 'Leonardo DiCaprio',
 'Brad Pitt',
 'Charlie Chaplin',

In [13]:
Lead_Actor_2

['Al Pacino',
 'Morgan Freeman',
 'Robert Duvall',
 'Ben Kingsley',
 'Kajol',
 'Miyu Irino',
 'John Fiedler',
 'Mone Kamishiraishi',
 'Lee Sun-kyun',
 'David Morse',
 'Heath Ledger',
 'Giulio Berruti',
 'Giulio Berruti',
 'Kim Seok-jin',
 'Samuel L. Jackson',
 'Eli Wallach',
 'Kim Seok-jin',
 'Robin Wright',
 'Ian McKellen',
 'Robert De Niro',
 'Giulio Berruti',
 'Jacques Perrin',
 'Nicoletta Braschi',
 'Takashi Shimura',
 'Akira Ishihama',
 'Janet Leigh',
 'James Woods',
 'Ayano Shiraishi',
 'Louise Fletcher',
 'Brad Pitt',
 'Selton Mello',
 'Uhm Ji-won',
 'Niall Horan',
 'Leandro Firmino',
 'Jake Johnson',
 'Hayato Taya',
 'Saori Hayami',
 'Takuya Kimura',
 'Harrison Ford',
 'Kim Seok-jin',
 'Ian McKellen',
 'Megumi Hayashibara',
 'Anne Hathaway',
 'Thomas Kretschmann',
 'Gloria Swanson',
 'Yuko Miyamura',
 'J.K. Simmons',
 'Ian McKellen',
 'Edward Furlong',
 'Grace Kelly',
 'James Stewart',
 'Haruo Tanaka',
 'Joseph Gordon-Levitt',
 'Morgan Freeman',
 'Jack Oakie',
 'Nataly Valencia

In [14]:
from itertools import chain
User_score=[]
user=soup.find_all('span', class_="icon")
user
#---------------------------------------------------------------
for score in user:
    score=re.findall(r'\d{2}', str(score))
    User_score.append(score)
#---------------------------------------------------------------
User_score=list(chain.from_iterable(User_score))
User_score

['87',
 '87',
 '86',
 '86',
 '86',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '85',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '84',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '83',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',
 '82',

In [15]:
#CLEAN YEAR, MONTH AND DAY COLUMNS IN ORDER******** AUTOMATIZADO
Date=[]
Date.append(soup.find_all('p'))
Date=Date[0]
Date
#---------------------------------------------------------------
Year=[]
Month=[]
Day=[]
count=0
from itertools import chain
#---------------------------------------------------------------
for years in Date:
    years=re.findall(r'\d{4}', re.sub('<.*?>','', str(years)))
    Year.append(years)
#---------------------------------------------------------------    
for days in Date:  
    days=re.findall(r'\d{2}?', re.sub('<.*?>','', str(days)))
    Day.append(days)
#---------------------------------------------------------------    
for months in Date:     
    months=re.findall(r'[A-Za-z]{3}', re.sub('<.*?>','', str(months)))
    Month.append(months)
#---------------------------------------------------------------    

Year=list(chain.from_iterable(Year))
#---------------------------------------------------------------
Day=list(chain.from_iterable(Day))
Day=Day[0:len(Day):3]
#---------------------------------------------------------------
Month=list(chain.from_iterable(Month))
del Month[0:2]
del Month[Month.index('Sea'):]
k='Loa'
while k in Month:
    Month.remove(k)
k='Mor'
while k in Month:
    Month.remove(k)

In [23]:
data={'Year':Year,
'Month': Month,
'Day' : Day,
'User Score': User_score,
'Title': Title_list,
'Genre': Genres,    
'Duration [minutes]': Durations,
'Director': Directors,
'Lead_Actor_1': Lead_Actor_1,
'Lead_Actor_2' : Lead_Actor_2,
'Budget [USD]' : Budgets,
'Revenue [USD]' : Revenues,
'Language' : Languages}

In [49]:
DF=pd.DataFrame(data)

for element in range(len(DF['Duration [minutes]'])):
    if len(DF['Duration [minutes]'][element])>4: #2h22m
        min_in_hour=int(DF['Duration [minutes]'][element][0])*60
        minutes=int(DF['Duration [minutes]'][element][-3:-1])
        DF['Duration [minutes]'][element]=min_in_hour+minutes
    elif len(DF['Duration [minutes]'][element])>3: #1h9m
        min_in_hour=int(DF['Duration [minutes]'][element][0])*60
        minutes=int(DF['Duration [minutes]'][element][-2:-1])
        DF['Duration [minutes]'][element]=min_in_hour+minutes
    elif len(DF['Duration [minutes]'][element])>2: #18m
        minutes=int(DF['Duration [minutes]'][element][-3:-1])
        DF['Duration [minutes]'][element]=minutes
    else:                                  #6m
        minutes=int(DF['Duration [minutes]'][element][-2:-1])
        DF['Duration [minutes]'][element]=minutes

In [53]:
Certifications=[]
def certification_function(x):
    response=requests.get(List_titles_url[x]).content
    source=bs(response,'html')
    certification=source.find_all('span',class_='certification')
    return certification

for num_title in range(len(List_titles_url)):
    Certifications.append(certification_function(num_title))
    Certifications[num_title]=re.sub(r'<(.+?)>|\s*|\W*?','',str(Certifications[num_title]))


In [57]:
DF['Classification']=Certifications

In [65]:
DF

Year Month Day User Score                                     Title  \
0     1972   Mar  14         87                      The Godfather (1972)   
1     1994   Sep  23         87           The Shawshank Redemption (1994)   
2     1974   Dec  20         86              The Godfather Part II (1974)   
3     1993   Dec  15         86                   Schindler's List (1993)   
4     1995   Oct  19         86        Dilwale Dulhania Le Jayenge (1995)   
...    ...   ...  ..        ...                                       ...   
3035  2013   Mar  15         69  The Wizards Return: Alex vs. Alex (2013)   
3036  1992   Jan  22         69                          The Lover (1992)   
3037  2021   Dec  05         69             The Tragedy of Macbeth (2021)   
3038  2017   Sep  13         69               Victoria &amp; Abdul (2017)   
3039  2011   Apr  15         69                Water for Elephants (2011)   

                                   Genre Duration [minutes]  \
0                         [Drama, Crime]                175   
1                         [Drama, Crime]                142   
2                         [Drama, Crime]                202   
3                  [Drama, History, War]                195   
4               [Comedy, Drama, Romance]                190   
...                                  ...                ...   
3035  [Family, Adventure, Comedy, Drama]                  1   
3036                    [Drama, Romance]                115   
3037                        [Drama, War]                105   
3038                    [Drama, History]                112   
3039                    [Drama, Romance]                122   

                  Director       Lead_Actor_1       Lead_Actor_2  \
0     Francis Ford Coppola      Marlon Brando          Al Pacino   
1           Frank Darabont        Tim Robbins     Morgan Freeman   
2     Francis Ford Coppola          Al Pacino      Robert Duvall   
3         Steven Spielberg        Liam Neeson       Ben Kingsley   
4            Aditya Chopra     Shah Rukh Khan              Kajol   
...                    ...                ...                ...   
3035       Victor Gonzalez       Selena Gomez     Jake T. Austin   
3036   Jean-Jacques Annaud         Jane March  Tony Leung Ka-fai   
3037             Joel Coen  Denzel Washington  Frances McDormand   
3038        Stephen Frears         Judi Dench          Ali Fazal   
3039            Sara Gruen   Robert Pattinson  Reese Witherspoon   

        Budget [USD]    Revenue [USD] Language Classification  
0      $6,000,000.00  $245,066,411.00  English              R  
1     $25,000,000.00   $28,341,469.00  English              B  
2     $13,000,000.00  $102,600,000.00  English              R  
3     $22,000,000.00  $321,365,567.00  English              R  
4     $13,200,000.00  $100,000,000.00    Hindi              G  
...              ...              ...      ...            ...  
3035               -                -  English             PG  
3036               -    $5,013,090.00   French              R  
3037               -                -  English              R  
3038               -   $65,421,267.00  English           PG13  
3039  $38,000,000.00  $117,094,902.00  English           PG13  

[3040 rows x 14 columns]

In [58]:
DF.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3040 entries, 0 to 3039
Data columns (total 14 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   Year                3040 non-null   object
 1   Month               3040 non-null   object
 2   Day                 3040 non-null   object
 3   User Score          3040 non-null   object
 4   Title               3040 non-null   object
 5   Genre               3040 non-null   object
 6   Duration [minutes]  3040 non-null   object
 7   Director            3040 non-null   object
 8   Lead_Actor_1        3040 non-null   object
 9   Lead_Actor_2        3040 non-null   object
 10  Budget [USD]        3040 non-null   object
 11  Revenue [USD]       3040 non-null   object
 12  Language            3040 non-null   object
 13  Classification      3040 non-null   object
dtypes: object(14)
memory usage: 332.6+ KB


In [59]:
DF.describe()

Year Month   Day User Score            Title    Genre  \
count   3040  3040  3040       3040             3040     3040   
unique   106    12    31         19             3040      969   
top     2019   Dec    25         70  Loveless (2017)  [Drama]   
freq     141   387   141        353                1      316   

        Duration [minutes]     Director Lead_Actor_1 Lead_Actor_2  \
count                 3040         3040         3040         3040   
unique                 184         1743         1712         2191   
top                    105  Woody Allen    Tom Hanks         None   
freq                    72           19           22           26   

       Budget [USD] Revenue [USD] Language Classification  
count          3040          3040     3040           3040  
unique          465          2062       32             51  
top               -             -  English              R  
freq           1025           885     2172            852

In [68]:
DF.to_csv('TopMoviesEDA.csv')